# Laboratorio Redes Neuronales

En esta clase vamos a tener la primera aproximación a redes neuronales utilizando Keras. En particular, vamos a tomar como guía el problema bien conocido de clasificación de dígitos escritos manualmente.  [Aquí](https://www.tensorflow.org/datasets/catalog/mnist?hl=es-419) pueden verse su características principales.

Keras es una biblioteca de Redes Neuronales de Código Abierto escrita en Python. Es una biblioteca de alto nivel, fácil de utilizar y muy popular. Puede utilizarse sobre otras bibliotecas o frameworks como Tensorflow, que provee funcionalidades y características adicionales.

Para comenzar, vamos a importar los módulos necesarios.

In [ ]:
import numpy as np
from tensorflow import keras
from keras.datasets import mnist
import matplotlib.pyplot as plt

A continuación cargamos el dataset. A diferencia de otros dataset que hemos usado, este ya viene divido en train y test, con 60.000 ejemplos de entrenamiento, y 10.000 en test.

In [ ]:
(x_train, y_train), (x_test, y_test) = mnist.load_data()
x_train.shape, x_test.shape

11490434/11490434 [==============================] - 2s 0us/step


((60000, 28, 28), (10000, 28, 28))

In [ ]:
# x_train es un array de numpy
type(x_train)

Veamos algunos ejemplos del conjunto de entrenaiento...

In [ ]:
plt.figure(figsize=(10,10))
for i in range(25):
    plt.subplot(5,5,i+1)
    plt.xticks([])
    plt.yticks([])
    plt.imshow(x_train[i], cmap='gray')
    plt.xlabel(y_train[i])
plt.show()

El dataset esta compuesto por imágenes de 28 x 28 pixeles en escala de grises, que sencillamente se representa como una matriz de enteros, de 28 x 28, cuyos valores van del 0 (negro absoluto) al 255 (completamente blanco).

De esta forma, x_train es de `(n_samples, height, weight)`.

In [ ]:
print('x_train es de ', x_train.shape)
print('x_test es de ', x_test.shape)
print('El tipo de datos es ', x_train.dtype)

Si inspeccionamos el primer ejemplo de entrenamiento, vemos que el valor de los pixeles efectivamente van de 0 a 255, y que es de 28 x 28

In [ ]:
plt.title("digito {}".format(y_train[0]))
plt.imshow(x_train[0], cmap='gray')
plt.colorbar()
plt.grid(False)
plt.show()

## Preprocesamiento de los datos
En la siguiente celda, vamos a preprocesar las imagenes que vamos a utilizar antes de comenzar el entrenamiento.

Para la mayoría de los datos de imágenes, los valores de píxeles son números enteros con valores entre 0 y 255.
Las redes neuronales procesan las entradas utilizando valores de peso pequeños, y las entradas con valores enteros grandes pueden interrumpir o ralentizar el proceso de aprendizaje. Como tal, es una buena práctica normalizar los valores de los píxeles para que cada valor de los píxeles tenga un valor entre 0 y 1. Además, para que no todas las entradas sean positivas podemos centrar la media a 0, favoreciendo el aprendizaje.

**Se pide**:
 - Utilizando la operacion `reshape`, convertir los ejemplos de entrenamiento de matriz a vector
 - Convertir el tipo de los datos de tipo `np.uint8` a `np.float32`
 - Dividimos el valor de cada pixel entre 255 para asegurar que todos los pixeles queden en el rango $[0,1]$
 - Restamos a cada pixel 0.5 para asegurar que todos los pixeles queden en el rango $[-0.5,0.5]$

 (Utilice variables x_train1 y x_test1 para no modificar el dataset original)



In [ ]:
######################################## COMPLETAR SEGÚN LO PEDIDO ##################################################


####################################################################################################################


In [ ]:
# Verificamos que los pasos anteriores fueron correctos
assert x_train1.ndim == 2, "Deben haber 2 dimensiones, hay {}".format(x_train1.ndim)
assert x_train1.min() == -.5, "El minimo debe ser -.5 pero es {}".format(x_train1.min())
assert x_train1.max() == .5, "El minimo debe ser .5 pero es {}".format(x_train1.max())

In [ ]:
# Cuando verificamos que quedó bien, modificamos los datos originales
x_train = x_train1
x_test = x_test1

**Se pide**: Utilizando el metodo `train_test_split` se scikit-learn, tomar el 90% del conjunto de entrenamiento para entrenar, y utilizar el restante para validar, que llamaremos `x_val`, `y_val`, y que vamos a usar para tunear parametros. Utilizamos un random_state=0 para asegurar reproductibilidad.

In [ ]:
from sklearn.model_selection import train_test_split

######################################## COMPLETAR SEGÚN LO PEDIDO ##################################################


####################################################################################################################

# Verificamos que todo este bien
assert len(x_train) == len(y_train)
assert len(x_val) == len(y_val)

In [ ]:
print(x_train.shape)
print(x_val.shape)

## Keras Sequential Models API
Keras provee dos grandes APIs para trabajar con modelos: secuencial y funcional. En esta clase vamos a trabajar con la primera de ellas: _Keras Sequential Models_. Esta API permite crear modelos de deep leaning a partir de una instancia de la clase `Sequential` a la que luego se le crean y agregan las capas necesarias.

Por ejemplo, las capas pueden ser definidas y pasadas a la clase Sequential como una lista:

```python
from keras.models import Sequential
from keras.layers import Dense
model = Sequential([Dense(2, activation="relu", input_dim=1, name="hidden_layer"),
                    Dense(1, activation="sigmoid", name="output_layer")], name="my_model")
```

O pueden ser agregadas de a una:

```python
from keras.models import Sequential
from keras.layers import Dense
model = Sequential(name="my_model")
model.add(Dense(2, activation="relu",  input_dim=1, name="hidden_layer"))
model.add(Dense(1, activation="sigmoid", name="output_layer"))
```

En ambos casos, `model` es una red neuronal con dos capas, donde la primera tiene dos neuronas (capa oculta), y la segunda (capa de salida) tiene solo una.
`Dense` es simplemente una capa densa, también conocida como completamente conectada (fully conected).

En ambos casos, para cada capa, se indica la función de activación a utilizar. Los nombres, tanto de las capas como del modelo, son strings arbitrarios (es decir, texto) que facilitan la comprensión del modelo.

Esta clase permite desarrollar modelos para la mayoría de las aplicaciónes que vamos a ver, es muy sencilla aunque tiene sus limitaciones (por ejemplo, unicamente permite crear modelos de tipo _feed forward_).

Una vez creado el modelo, se puede ver un resumen de este con el método `summary`:
```python
model.summary()

```
Que muestra lo siguiente:
```
Model: "my_model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
=================================================================
hidden_layer (Dense)         (None, 2)                 4         
_________________________________________________________________
output_layer (Dense)         (None, 1)                 3         
=================================================================
Total params: 7
Trainable params: 7
Non-trainable params: 0
```




### Para la entrega: Contestar las siguientes preguntas

- ¿Cuál es la dimensión de la entrada?
- ¿por qué los parámetros de la primera capa son 4?
- ¿Por qué los de la segunda son 3?



### Construir el modelo

**Se pide:** definir un modelo completamente conectado, que en su capa oculta tenga 32 neuronas, y su capa de salida 10 (una para cada dígito). La capa oculta utilizará un función sigmoide, mientras que la capa de salida debe utilizar como activación la función softmax. Mostrar el resumen para el modelo dado. Cree el modelo utilizando una lista de capas y muestre el resultado

In [ ]:
from keras.models import Sequential
from keras.layers import Dense

######################################## COMPLETAR SEGÚN LO PEDIDO ##################################################

##########################################################################################


### Compilar el modelo
Luego que el modelo es definido, antes de pasar al entrenamiento, se necesita configurar algunas cosas más, que se agregan durante el paso de compilación:
 - *loss function*: función de error a minimizar. Usualmente nos referimos a ella como _loss_ o _pérdida_
 - *optimizer*: algoritmo utilizado para optimizar la función. Esto es, qué algoritmo de descenso por gradiente utilizar. Debe ser un objeto del módulo [optimizers](https://keras.io/optimizers), instanciado con los parámetros deseados, o un string indicando cuál utilizar, en cuyo caso se utilizan los valores por defecto.
 - *metrics*: métricas a ser usadas para monitorear la evolución del entrenamiento. En este ejemplo, se utiliza el acierto (accuracy)

```python
from keras.optimizers import SGD
model.compile(optimizer=SGD(lr=0.000001),
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
```
**Se pide:** Compilar el modelo con la función [compile](https://keras.io/models/sequential/#compile), utilizando como optimizador una instancia de SGD, que tenga *learning rate* (`lr=0.01`), y los demás parámetros como en el ejemplo dado.

In [ ]:
from keras.optimizers import SGD

######################################## COMPLETAR SEGÚN LO PEDIDO ##################################################


##########################################################################################



### Entrenar el modelo
Este paso es en el que efectivamente se entrena la red. Se deben indicar algunos parámetros más, como los ejemplos de entrenamiento y validación, la cantidad de épocas y el tamaño del batch. Todo esto se hace con la función [fit](https://keras.io/api/models/model_training_apis/#fit-method).

- Epoch = una pasada hacia adelante y una pasada hacia atrás de todos los ejemplos de entrenamiento
- Batch Size = el número de ejemplos de entrenamiento en una pasada forward/backward.
- Iteración = una iteración realiza una pasada forward/backward de “Batch Size” número de ejemplos.

Ejemplo: si tiene 1000 ejemplos de entrenamiento y el tamaño del batch es 500, se necesitarán 2 iteraciones para completar 1 época.

El término "Batch" es ambiguo: algunas personas lo usan para designar el conjunto de entrenamiento completo, y algunas personas lo usan para referirse a la cantidad de ejemplos de entrenamiento en una pasada forward/backward. Para evitar esa ambigüedad y dejar en claro que el Batch corresponde al número de ejemplos de entrenamiento en una pasada forward/backward, se puede usar el término mini Batch.

**Se pide**: entrenar el modelo con un batch_size de 32, durante 10 épocas. Utilice los datos de validación para ver la evolución de la accuracy.

In [ ]:
######################################## COMPLETAR SEGÚN LO PEDIDO ##################################################


##########################################################################################


### Preguntas a contestar
- En nuestro entrenamiento: ¿Cuántas iteraciones tendremos por época?
- ¿En cada época se usan los mismos ejemplos de entrenamiento? ¿Por qué será?

____________________________________________________________________________________

Durante el entrenamiento, se muestra el progreso en salida estándar. Una vez terminado, es importante visualizar cómo evolucionó el modelo durante el entrenamiento. El comportamiento de las distintas métricas durante el entrenamiento arrojan pistas sobre qué está pasando.

En model.history queda el registro histórico de qué sucedió con la `accuracy` y `loss` durante el entrenamiento para ambos conjuntos.

In [ ]:
def plot_history(history):
    # Plot training & validation accuracy values
    plt.plot(history.history['accuracy'])
    plt.plot(history.history['val_accuracy'])
    plt.title('Model accuracy')
    plt.ylabel('Accuracy')
    plt.xlabel('Epoch')
    plt.legend(['Train', 'Validation'], loc='upper left')
    plt.show()

    # Plot training & validation loss values
    plt.plot(history.history['loss'])
    plt.plot(history.history['val_loss'])
    plt.title('Model loss')
    plt.ylabel('Loss')
    plt.xlabel('Epoch')
    plt.legend(['Train', 'Validation'], loc='upper left')
    plt.show()
    plt.clf()

# Invocamos a la función plot_history para ver cómo se comportó
plot_history(model.history)

### Pregunta a contestar
¿Qué conclusiones sacamos de nuestro primer modelo elegido? ¿Está aprendiendo?

### Predecir
Una vez que tenemos el modelo entrenado, es interesante hacer predicciones sobre distintas instancias. Para esto se cuenta con el método `predict`. Este método nos devuelve una matriz de dimenciones (n_samples, n_classes), donde cada fila contiene el valor de la función softmax para cada instancia clasificada.

In [ ]:
predictions = model.predict(x_val)
predictions.shape


El siguiente vector contiene la predicción para el primer ejemplo de evaluación. El valor de cada entrada se puede interpretar como una probabilidad, y cada entrada de este vector contiene la probabilidad de que el ejemplo pertenezca a la respectiva clase.

In [ ]:
predictions[0]

Utilizando la función de numpy np.argmax podemos obtener, para cada instancia, cuál es la clase que tiene mayor probabilidad, y utilizar esta clase como nuestra predicción

In [ ]:
y_val_pred = np.argmax(predictions, axis=1)
y_val_pred

array([3, 6, 6, ..., 7, 6, 5])

**Se pide**: imprimir imagen del primer ejemplo de x_val y valor de predicción de nuestro modelo para dicha imagen. ¿El modelo funcionó bien?

In [ ]:
######################################## COMPLETAR SEGÚN LO PEDIDO ##################################################


##########################################################################################


Una vez que tenemos las predicciones hechas por la red, y sus valores reales, se puede utilizar cualquier métrica del módulo [sklearn.metrics](https://scikit-learn.org/stable/modules/classes.html#module-sklearn.metrics) que hemos usado antes:

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(y_val, y_val_pred))

En este punto se espera que tengan un manejo mínimo de keras como para entrenar un modelo. En los próximos pasos, el objetivo es entender qué efecto tiene cada parámetro.

#### Learning Rate

**Se pide**: Implementar un modelo  igual al anterior, pero cambiando la función de activación a relu. Entrenarlo durante 10 épocas, con `lr=2`, `lr=.01` y `lr=1e-6`. En cada caso graficar la evolución del error durante el entrenamiento. ¿Qué diferencias se observan? ¿A qué se atribuye? ¿Cuál funciona mejor?

In [ ]:
for lr in [2,.01,1e-6]:
    print('Probamos lr={}'.format(lr))
    # DEFINIR EL MODELO


    # COMPILARLO CON EL LR ADECUADO

    # ENTRENAR

    # MOSTRAR HISTÓRICO DE ENTRENAMIENTO


### Regularización

En la siguiente sección, vamos a robustecer al modelo, utilizando regularización L2 en su capa oculta. Esto es, dada la función de costo que estamos minimizando:
$$L(W) = \sum_{i=1}^{n} L_i(W) $$
agregar una penalizacion a los pesos
$$L(W) = \sum_{i=1}^{n} L_i(W)+ \lambda \frac{1}{2} |W|^{2}_{2}$$

Se encuentra [implementado en keras](https://keras.io/regularizers/) en el modulo `regularizers`, y hay que pasarlo como parametro al crear la capa oculta que se desea regularizar:

```python
from keras import regularizers
model.add(Dense(64, input_dim=64, activation="sigmoid",
                kernel_regularizer=regularizers.l2(0.01)))
```

El único parámetro que recibe es el $\lambda$, que indica cuanto peso tiene la regularización.

**Se pide**: Entrenar el modelo con el learning rate seleccionado el paso anterior, utilizando $\lambda = 1$ y $\lambda=1e-3$. En ambos casos, graficar la evolución del error.
¿Qué diferencias se observan? ¿A qué se atribuye? ¿Cuál funciona mejor?

In [ ]:
from keras import regularizers

for l in [1,1e-3]:
    print('Probamos l={}'.format(l))
    # DEFINIR EL MODELO



    # COMPILAR EL MODELO


    # ENTRENAR EL MODELO

    # MOSTRAR HISTÓRICO DE ENTRENAMIENTO


### Más capas, menos neuronas...

Implementar un modelo similar al anterior, pero que en vez de tener una única capa oculta con 32 neuronas, contenga 3 capas ocultas con 5 neuronas cada una.

Compilarlo, y entrenarlo con la misma configuración usada en pasos anteriores (utilice sigmoid en la primera capa oculta, y relu en las restantes). Mostrar cómo cambió su desempeño durante el entrenamiento. Mostrar el resumen del modelo con `model.summary()`

In [ ]:


# DEFINIR EL MODELO Y MOSTRAR EL RESUMEN



# COMPILAR EL MODELO


# ENTRENAR EL MODELO

# MOSTRAR HISTÓRICO DE ENTRENAMIENTO


### Batch normalization

A continuación, vamos a aplicar batch normalization (una forma de regularización) al modelo anterior.

Batch normalization debe ser aplicado inmediatamente **después** de computar las preactivacion, pero **antes** de aplicar la función de activación. Sin embargo, en los ejemplos vistos, ambas operaciones la ejecuta la misma capa:

```python
model.add(Dense(64, input_dim=64, activation="sigmoid",
      kernel_regularizer=regularizers.l2(0.01)))
```

Para aplicar batch normalization, se debe utilizar una funcion de activacion lineal en la capa densa, luego agregar la capa de batch normalization, y por ultimo agregar explicitamente la capa de activacion que querramos usar. El ejemplo anterior, se reescribe como sigue:

```python
from keras.layers import Activation
from keras.layers.normalization import BatchNormalization

model.add(Dense(64, input_dim=64, # no especificar activacion!
          kernel_regularizer=regularizers.l2(0.01)))
model.add(BatchNormalization())
model.add(Activation('sigmoid'))

```

**Opcional: se pide:** Entrenar nuevamente el modelo, esta vez agregando batch normalization a cada capa. Mostrar el desarrollo del entrenamiento y el resumen del modelo. ¿Qué se puede decir de este modelo en comparación con el anterior? ¿y con los anteriores a este? (1 capa oculta de 32 neuronas)

In [ ]:
from keras.layers import Activation
from keras.layers import BatchNormalization

# DEFINIR EL MODELO Y MOSTRAR RESUMEN




# COMPILAR EL MODELO

# ENTRENAR EL MODELO

# MOSTRAR ENTRENAMIENTO


**OPCIONAL: Se pide:** Repetir el experimento anterior, cambiando la función de activación a sigmoid, pero utilizar como algoritmo de descenso por gradiente Rmsprop, con sus parámetros por defecto.

Comparar resultados con el escenario anterior.

In [ ]:
from keras.optimizers import RMSprop


# DEFINIR EL MODELO


# COMPILAR EL MODELO

# ENTRENAR EL MODELO

# MOSTRAR HISTÓRICO DE ENTRENAMIENTO


**Dropout** Dropout es una capa muy sencilla de utilizar. Simplemente se agrega luego de la capa de activación como una capa más, indicanto la proporción de neuronas que se desean eliminar:

```python
from keras.layers import Dropout

model.add(Dropout(.2))  # 20%

```

**Early stopping** Keras permite definir diferentes [_callbacks_](https://keras.io/callbacks/). Esto son funciones auxiliares que se ejecutan durante el entrenamiento, al terminar un batch o una epoca. Esto es muy util para monitorear el entrenamiento, y entre otras cosas implementa EarlyStopping.

Se debe definir una lista con los callbacks a ser ejecutados, y luego se pasa esta lista al metodo fit.

```python
from keras.callbacks import EarlyStopping
ea = EarlyStopping(monitor='val_loss',
                   patience=2,
                   restore_best_weights=True)

cb_list = [ea] # lista de callbacks

model.fit(x_train, y_train,
          validation_data=[x_val, y_val],
          epochs=10, batch_size=32, callbacks=cb_list);

```

**OPCIONAL: Se pide**:
Probar los métodos de DropOut y Eary Stopping. Luego, Utilizando las herramientas vistas hasta el momento, entrenar el mejor modelo posible, que tenga 2 capas ocultas.

In [ ]:
from keras.layers import Dropout
from keras.callbacks import EarlyStopping

ea = EarlyStopping(monitor='val_loss', patience=2, restore_best_weights=True)
cb_list = [ea] # lista de callbacks

lr = .01

# DEFINIR EL MODELO


# COMPILAR EL MODELO

# ENTRENAR EL MODELO

# MOSTRAR LA HISTORIA DE APRENDIZAJE



Reportar la performance del mejor modelo encontrado sobre el conjunto de test.

In [ ]:
# De todos los modelos que hice, entreno sobre el conjunto de entrenamiento el mejor
# Que fue el original, con lr = 0.001

# DEFINIR EL MODELO


# COMPILAR EL MODELO


# ENTRENAR EL MODELO

# MOSTRAR HISTÓRICO DE ENTRENAMIENTO

# Hacer las predicciones y mostrar el reporte sobre conjunto de test

